<a href="https://colab.research.google.com/github/oscarserc/LENGUAJE_NLP/blob/main/Transformers_2_HuggingFace_EstructuraInterna.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:

# -----------------------------------------------------------
# PRACTICAS DE: Natural Language Processing with Transformers
# -----------------------------------------------------------

# GitHub del libro: https://github.com/nlp-with-transformers/notebooks

# Uncomment and run this cell if you're on Colab or Kaggle
!git clone https://github.com/nlp-with-transformers/notebooks.git
%cd notebooks
from install import *
install_requirements()


Cloning into 'notebooks'...
remote: Enumerating objects: 421, done.
remote: Counting objects: 100% (5/5), done.
remote: Compressing objects: 100% (5/5), done.
remote: Total 421 (delta 0), reused 5 (delta 0), pack-reused 416
Receiving objects: 100% (421/421), 24.97 MiB | 19.93 MiB/s, done.
Resolving deltas: 100% (190/190), done.
/content/notebooks
⏳ Installing base requirements ...
✅ Base requirements installed!
⏳ Installing Git LFS ...
✅ Git LFS installed!


#**Utilizamos la librería BERTVIZ para la visualización de los resultados internos del TRANSFORMER**.

In [ ]:

from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

# CODIGO DEL TRANSFORMER
model_ckpt = 'bert-base-uncased'

# INSTANCIAMOS EL TOKENIZADOR y EL MODELO
tokenizer  = AutoTokenizer.from_pretrained(model_ckpt)
model      = BertModel.from_pretrained(model_ckpt)

# TEXTO
text = 'Times flies like an arrow'

# Desplazar el cursor por las palabras para ver la intensidad con la que están relacionadas entre sí
# (SI PULSAMOS EL SIGNO '+' DEL LATERAL IZQUIERDO DE LA PALABRA: se obtiene cómo se generan los valores con las KEYS, QUERIES y VALUES)
show(model, 'bert', tokenizer, text, display_mode='light', layer=0, head=8)


Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/455k [00:00<?, ?B/s]

100%|██████████| 440473133/440473133 [00:11<00:00, 39660904.47B/s]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#Tokenizamos y convertimos en NÚMEROS ENTEROS cada token.

In [ ]:

from transformers import AutoTokenizer

# CÓDIGO DEL TRANSFORMER
model_ckpt = 'bert-base-uncased'

# Tokenizador
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

# EJEMPLO DE TEXTO
text       = 'time flies like an arrow'

# ESTRUCTURA QUE GENERA EL TOKENIZADOR
#      · 'input_ids' 
#      · 'token_type_ids'
#      · 'attention_mask'
inputs = tokenizer(text, return_tensors='pt', add_special_tokens=False)
inputs

# Para acceso a cada una de las partes:
#   inputs.input_ids
#   inputs.token_type_ids
#   inputs.attention_mask

{'input_ids': tensor([[ 2051, 10029,  2066,  2019,  8612]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1]])}

#Procedemos a generar el EMBEDDING (proyección a un espacio de alta dimensión)

In [ ]:

from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb



Embedding(30522, 768)

In [ ]:

# Probamos con el texto anterior
inputs_embeds = token_emb(inputs.input_ids)
# El tensor de 5 números enteros lo convierte en 5 tensores de 768 dimensiones
# inputs_embeds.size():  torch.Size([1, 5, 768])
inputs_embeds


tensor([[[-0.0259, -0.3105, -0.0356,  ..., -0.9442, -0.2247,  1.1133],
         [ 1.0205,  1.3155,  0.3781,  ...,  0.0044, -0.7677,  0.4467],
         [ 0.7590, -1.2727, -2.3936,  ..., -0.9353,  0.4728, -0.5324],
         [-1.7605,  1.9733, -0.0552,  ..., -0.4370,  0.5636,  1.2872],
         [ 0.0543, -0.0937, -0.3682,  ...,  0.8091,  1.2404,  1.0039]]],
       grad_fn=<EmbeddingBackward0>)

#Procedemos a generar las matrices KEYS, QUERIES y VALUES. 
(*Le asignamos el valor del INPUT EMBEDDING*).
#Calculamos los SCORES.

In [ ]:

import torch
from math import sqrt

query = key = value = inputs_embeds
# key.size() > torch.Size([1, 5, 768])
# Accedemos a la última dimensión para el ESCALADO de los datos: key.size(-1) ----> 768
dim_k = key.size(-1)

# CALCULO DE LOS SCORES
# ---------------------
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
# key.size()                 ----> torch.Size([1, 5, 768])
# key.transpose(1,2).size()  ----> torch.Size([1, 768, 5])

scores.size()


torch.Size([1, 5, 5])

#Calculamos los PESOS.

In [ ]:

import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)


tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

#Calculamos la ATENCIÓN.

In [ ]:

# CALCULAMOS LA ATENCIÓN
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape


torch.Size([1, 5, 768])

#**Creamos un procedimiento para el cálculo de la SCALED DOT PRODUCT ATTENTION que acabamos de ver por pasos**.

In [ ]:

# SCALED DOT-PRODUCT-ATTENTION
# ============================

def scaled_dot_product_attention(query, key, value):
  dim_k   = query.size(-1)
  scores  = torch.bmm(query,key.transpose(1,2)) / sqrt(dim_k)
  weights = F.softmax(scores, dim=-1)

  return torch.bmm(weights, value)


#========================

#**Generamos manualmente las clases para construir la estructura de MULTI HEAD ATTENTION**.

In [ ]:

# Modulo para la cabeza de ATENCIÓN
# ---------------------------------

class AttentionHead(nn.Module):
  def __init__(self, embed_dim, head_dim):
    super().__init__()
    self.q = nn.Linear(embed_dim, head_dim)
    self.k = nn.Linear(embed_dim, head_dim)
    self.v = nn.Linear(embed_dim, head_dim)

  def forward(self, hidden_state):
    attn_outputs = scaled_dot_product_attention(self.q(hidden_state),
                                                self.k(hidden_state),
                                                self.v(hidden_state))
    return attn_outputs  


In [ ]:

# Configuramos las múltiples CABEZAS LECTORAS del mecanismo de ATENCIÓN
# ---------------------------------------------------------------------

class MultiHeadAttention(nn.Module):
  def __init__(self, config):
    super().__init__()
    embed_dim = config.hidden_size
    num_heads = config.num_attention_heads
    head_dim  = embed_dim // num_heads
    self.heads = nn.ModuleList(
        [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
    )
    self.output_linear = nn.Linear(embed_dim, embed_dim)

  def forward(self, hidden_state):
    x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
    x = self.output_linear(x)
    return x  


In [ ]:

multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()


torch.Size([1, 5, 768])

In [ ]:

from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

# TEXTO
# -----
frase_1 = 'time flies like an arrow'
frase_2 = 'fruit flies like a banana'

viz_inputs = tokenizer(frase_1, frase_2, return_tensors='pt')
attention  = model(**viz_inputs).attentions
frase_2_inicio = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, frase_2_inicio, heads=[8])


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<IPython.core.display.Javascript object>

#Ahora construimos la capa FEED FORWARD.

In [ ]:

class FeedForward(nn.Module):
  def __init__(self, config):
    super().__init__()
    self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
    self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
    self.gelu = nn.GELU()
    self.dropout = nn.Dropout(config.hidden_dropout_prob)

  def forward(self, x):
    x = self.linear_1(x)
    x = self.gelu(x)
    x = self.linear_2(x)
    x = self.dropout(x)
    return x  


In [ ]:

feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()


torch.Size([1, 5, 768])

#Configuramos la capa ENCODER.

In [ ]:

class TransformerEncoderLayer(nn.Module):
  def __init__(self, config):
    super().__init__()
    self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
    self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
    self.attention = MultiHeadAttention(config)
    self.feed_forward = FeedForward(config)

  def forward(self, x):
    # Aplicamos la NORMALIZACIÓN y después copiamos en las QUERY, KEY, VALUE
    hidden_state = self.layer_norm_1(x)
    # Aplicamos el mecanismo de ATENCIÓN con una 'skip conection'
    x = x + self.attention(hidden_state)
    # Aplicamos la capa FEED-FORWARD con una 'skip contection'
    x = x + self.feed_forward(self.layer_norm_2(x))
    return x  


In [ ]:

encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()


(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

#Introducimos el POSITIONAL EMBEDDING.

In [ ]:

class Embeddings(nn.Module):
  def __init__(self, config):
    super().__init__()
    self.token_embeddings = nn.Embedding(config.vocab_size,
                                         config.hidden_size)
    self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                            config.hidden_size)
    self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
    self.dropout = nn.Dropout()

  def forward(self, input_ids):
    # Creamos IDs de posición para la secuencia de entrada
    seq_length   = input_ids.size(1)
    position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
    # Creamos los EMBEDDING de TOKEN y POSICIÓN
    token_embeddings    = self.token_embeddings(input_ids)
    position_embeddings = self.position_embeddings(position_ids)
    # Combinamos los EMBEDDING de TOKEN y POSICIÓN
    embeddings = token_embeddings + position_embeddings
    embeddings = self.layer_norm(embeddings)
    embeddings = self.dropout(embeddings)
    return embeddings


In [ ]:

embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()


torch.Size([1, 5, 768])

#Configuramos la parte ENCODER del TRANSFORMER.

In [ ]:

class TransformerEncoder(nn.Module):
  def __init__(self, config):
    super().__init__()
    self.embeddings = Embeddings(config)
    self.layers     = nn.ModuleList([TransformerEncoderLayer(config) for _ in range(config.num_hidden_layers)])

  def forward(self, x):
    x = self.embeddings(x)
    for layer in self.layers:
      x = layer(x)

    return x    


In [ ]:

encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()


torch.Size([1, 5, 768])

#Añadimos la CABEZA DE CLASIFICACIÓN.

In [ ]:

class TransformerForSequenceClassification(nn.Module):
  def __init__(self, config):
    super().__init__()
    self.encoder = TransformerEncoder(config)
    self.dropout = nn.Dropout(config.hidden_dropout_prob)
    self.classifier = nn.Linear(config.hidden_size, config.num_labels)

  def forward(self, x):  
    # Primero seleccionamos el ESTADO OCULTO del token [CLS]
    x = self.encoder(x)[:, 0, :]
    # ------------------------------------------------------
    x = self.dropout(x)
    x = self.classifier(x)
    return x


In [ ]:

config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()


torch.Size([1, 3])